In [1]:
# upgrade in command line for specific interpreter

import sys
sys.executable
# /Users/lianfeng/Document/species_richness_sdm/venv/bin/pip install --upgrade tensorflow

'/Users/lianfeng/miniconda3/envs/tf/bin/python'

In [2]:
# 
exec('from __future__ import absolute_import, division, print_function, unicode_literals')

import numpy as np
import datetime
import pathlib
from sqlalchemy import create_engine
import matplotlib.pyplot as plt
import pandas as pd
import seaborn as sns
from sklearn.model_selection import train_test_split
from sklearn import preprocessing
from sklearn.preprocessing import MinMaxScaler
from sklearn.impute import KNNImputer

from tensorflow import keras
from tensorflow.keras import layers
from tensorflow.keras.layers import Dense, Activation, Dropout

In [3]:
from hyperopt import Trials, STATUS_OK, tpe
from hyperas import optim
from hyperas.distributions import choice, uniform

Using TensorFlow backend.


In [4]:
def data():
    localhost = {'user': 'postgres', 'password': 'postgres', 'host': 'localhost', 'port': 5432, 'db': 'fiadb'}
    params = 'postgresql://{0}:{1}@{2}:{3}/{4}'
    engine = create_engine(params.format(localhost['user'], localhost['password'], localhost['host'], localhost['port'], localhost['db']))
    pergrid_base = """select distinct * from predictor.pergrid_base_eus"""
    pergrid_base_df = pd.read_sql(pergrid_base, engine)

    # separate predictor variables from outcome varaible
    y = pergrid_base_df['tsr']
    grid_id = pergrid_base_df['grid_id']
    pred_var= ['aet', 'ai', 'art', 'ewd', 'fa', 'map', 'mat', 'mpdq',
           'mtcq', 'pet', 'psn', 'ra', 'rmap', 'rmat', 'tsn', 'mfdf', 'alt','shg','mtwq','wa']
    pergrid_base_pred_df = pergrid_base_df[pred_var]

    # fill NaN with values from neighbor pixels
    imputer = KNNImputer(n_neighbors=5)
    pergrid_base_filled = imputer.fit_transform(pergrid_base_pred_df)
    pergrid_base_df = pd.DataFrame(pergrid_base_filled)
    pergrid_base_df.head()

    ss = MinMaxScaler()
    X_std = ss.fit_transform(pergrid_base_df)

    Xstd=pd.DataFrame(data=X_std[0:,0:],
                    index=pergrid_base_pred_df.index,
                    columns=pred_var)

    x_train, x_test, y_train, y_test = train_test_split(Xstd, y, test_size=0.1, random_state=12345)
    x_train, x_val, y_train, y_val = train_test_split(x_train, y_train, test_size=0.1, random_state=12345)

    return x_train, x_val, x_test, y_train, y_val, y_test

In [5]:
X_train, X_val, X_test, Y_train, Y_val, Y_test = data()

In [6]:
def create_model(x_train, y_train, x_val, y_val):

    model = keras.Sequential()
    model.add(layers.Dense({{choice([256, 512, 1024])}}, input_shape=(x_train.shape[1],)))  # tune # of units
    model.add(Activation({{choice(['relu'])}}))  # tune the activation function
    model.add(Dropout({{uniform(0, 1)}}))  # tune dropout rate

    model.add(Dense({{choice([256, 512, 1024])}}))
    model.add(Activation({{choice(['relu'])}}))
    model.add(Dropout({{uniform(0, 1)}}))
    
    model.add(Dense({{choice([256, 512, 1024])}}))
    model.add(Activation({{choice(['relu'])}}))
    model.add(Dropout({{uniform(0, 1)}}))

    # tune # of layers
    if {{choice(['three', 'four'])}} == 'four':
        model.add(Dense({{choice([256, 512, 1024])}}))
        model.add(Activation({{choice(['relu'])}}))
        model.add(Dropout({{uniform(0, 1)}}))

    model.add(Dense(1))
    model.add(Activation('linear'))

    # tune the optimizer and the learning rate
    adam = keras.optimizers.Adam(lr={{choice([10 ** -4, 10 ** -3, 10 ** -2])}})
    rmsprop = keras.optimizers.RMSprop(lr={{choice([10 ** -3, 10 ** -2, 10 ** -1])}})
    sgd = keras.optimizers.SGD(lr={{choice([10 ** -3, 10 ** -2, 10 ** -1])}})

    choiceval = {{choice(['adam', 'sgd', 'rmsprop'])}}
    if choiceval == 'adam':
        optim = adam
    elif choiceval == 'rmsprop':
        optim = rmsprop
    else:
        optim = sgd

    model.compile(loss='mae', metrics=['mean_absolute_error'], optimizer=optim)
    result=model.fit(x_train, y_train,
              batch_size={{choice([128, 256, 512])}},
              epochs=1000,
              verbose=2,
              validation_data=(x_val, y_val))
    
    mae, mse = model.evaluate(x_val, y_val, verbose=0)
    return {'loss': mae, 'status': STATUS_OK, 'model': model}

In [7]:
best_run, best_model = optim.minimize(model=create_model,
                                      data=data,
                                      algo=tpe.suggest,
                                      max_evals=30,
                                      trials=Trials(),
                                      notebook_name='ffnn')

>>> Imports:
#coding=utf-8

try:
    import sys
except:
    pass

try:
    import numpy as np
except:
    pass

try:
    import datetime
except:
    pass

try:
    import pathlib
except:
    pass

try:
    from sqlalchemy import create_engine
except:
    pass

try:
    import matplotlib.pyplot as plt
except:
    pass

try:
    import pandas as pd
except:
    pass

try:
    import seaborn as sns
except:
    pass

try:
    from sklearn.model_selection import train_test_split
except:
    pass

try:
    from sklearn import preprocessing
except:
    pass

try:
    from sklearn.preprocessing import MinMaxScaler
except:
    pass

try:
    from sklearn.impute import KNNImputer
except:
    pass

try:
    from tensorflow import keras
except:
    pass

try:
    from tensorflow.keras import layers
except:
    pass

try:
    from tensorflow.keras.layers import Dense, Activation, Dropout
except:
    pass

try:
    from hyperopt import Trials, STATUS_OK, tpe
except:
    pass

try:
    from hyperas im

Epoch 13/1000                                         
6174/6174 - 3s - loss: 7.1236 - mean_absolute_error: 7.1236 - val_loss: 5.1589 - val_mean_absolute_error: 5.1589

Epoch 14/1000                                         
6174/6174 - 2s - loss: 7.0673 - mean_absolute_error: 7.0673 - val_loss: 6.2513 - val_mean_absolute_error: 6.2513

Epoch 15/1000                                         
6174/6174 - 2s - loss: 6.7879 - mean_absolute_error: 6.7879 - val_loss: 5.0684 - val_mean_absolute_error: 5.0684

Epoch 16/1000                                         
6174/6174 - 2s - loss: 6.8173 - mean_absolute_error: 6.8173 - val_loss: 7.2567 - val_mean_absolute_error: 7.2567

Epoch 17/1000                                         
6174/6174 - 2s - loss: 6.4232 - mean_absolute_error: 6.4232 - val_loss: 4.9413 - val_mean_absolute_error: 4.9413

Epoch 18/1000                                         
6174/6174 - 2s - loss: 6.2923 - mean_absolute_error: 6.2923 - val_loss: 5.1314 - val_mean_absolute_e

6174/6174 - 2s - loss: 4.8406 - mean_absolute_error: 4.8406 - val_loss: 5.7389 - val_mean_absolute_error: 5.7389

Epoch 62/1000                                         
6174/6174 - 2s - loss: 4.8185 - mean_absolute_error: 4.8185 - val_loss: 5.8318 - val_mean_absolute_error: 5.8318

Epoch 63/1000                                         
6174/6174 - 2s - loss: 4.7989 - mean_absolute_error: 4.7989 - val_loss: 5.1138 - val_mean_absolute_error: 5.1138

Epoch 64/1000                                         
6174/6174 - 2s - loss: 4.8495 - mean_absolute_error: 4.8495 - val_loss: 5.6760 - val_mean_absolute_error: 5.6760

Epoch 65/1000                                         
6174/6174 - 2s - loss: 4.8555 - mean_absolute_error: 4.8555 - val_loss: 5.4592 - val_mean_absolute_error: 5.4592

Epoch 66/1000                                         
6174/6174 - 2s - loss: 4.7637 - mean_absolute_error: 4.7637 - val_loss: 5.7457 - val_mean_absolute_error: 5.7457

Epoch 67/1000                            

Epoch 110/1000                                        
6174/6174 - 2s - loss: 4.6602 - mean_absolute_error: 4.6602 - val_loss: 4.8954 - val_mean_absolute_error: 4.8954

Epoch 111/1000                                        
6174/6174 - 2s - loss: 4.5976 - mean_absolute_error: 4.5976 - val_loss: 5.0359 - val_mean_absolute_error: 5.0359

Epoch 112/1000                                        
6174/6174 - 2s - loss: 4.6820 - mean_absolute_error: 4.6820 - val_loss: 4.6954 - val_mean_absolute_error: 4.6954

Epoch 113/1000                                        
6174/6174 - 2s - loss: 4.6387 - mean_absolute_error: 4.6387 - val_loss: 5.3908 - val_mean_absolute_error: 5.3908

Epoch 114/1000                                        
6174/6174 - 2s - loss: 4.6775 - mean_absolute_error: 4.6775 - val_loss: 5.2768 - val_mean_absolute_error: 5.2768

Epoch 115/1000                                        
6174/6174 - 2s - loss: 4.6622 - mean_absolute_error: 4.6622 - val_loss: 5.4849 - val_mean_absolute_e

6174/6174 - 2s - loss: 4.5925 - mean_absolute_error: 4.5925 - val_loss: 4.5266 - val_mean_absolute_error: 4.5266

Epoch 159/1000                                        
6174/6174 - 2s - loss: 4.6255 - mean_absolute_error: 4.6255 - val_loss: 5.7339 - val_mean_absolute_error: 5.7339

Epoch 160/1000                                        
6174/6174 - 2s - loss: 4.5928 - mean_absolute_error: 4.5928 - val_loss: 4.7836 - val_mean_absolute_error: 4.7836

Epoch 161/1000                                        
6174/6174 - 2s - loss: 4.5910 - mean_absolute_error: 4.5910 - val_loss: 4.8139 - val_mean_absolute_error: 4.8139

Epoch 162/1000                                        
6174/6174 - 2s - loss: 4.5824 - mean_absolute_error: 4.5824 - val_loss: 5.6373 - val_mean_absolute_error: 5.6373

Epoch 163/1000                                        
6174/6174 - 2s - loss: 4.5713 - mean_absolute_error: 4.5713 - val_loss: 5.5215 - val_mean_absolute_error: 5.5215

Epoch 164/1000                           

...

Epoch 803/1000                                                                      
6174/6174 - 1s - loss: 2.8478 - mean_absolute_error: 2.8478 - val_loss: 4.6897 - val_mean_absolute_error: 4.6897

Epoch 804/1000                                                                      
6174/6174 - 1s - loss: 2.8859 - mean_absolute_error: 2.8859 - val_loss: 4.5395 - val_mean_absolute_error: 4.5395

Epoch 805/1000                                                                      
6174/6174 - 1s - loss: 2.8680 - mean_absolute_error: 2.8680 - val_loss: 4.7264 - val_mean_absolute_error: 4.7264

Epoch 806/1000                                                                      
6174/6174 - 1s - loss: 2.9009 - mean_absolute_error: 2.9009 - val_loss: 4.7311 - val_mean_absolute_error: 4.7311

Epoch 807/1000                                                                      
6174/6174 - 1s - loss: 2.9103 - mean_absolute_error: 2.9103 - val_loss: 4.6027 - val_mean_absolute_error: 4.6027

Epoch

Epoch 844/1000                                                                      
6174/6174 - 1s - loss: 2.8316 - mean_absolute_error: 2.8316 - val_loss: 5.0372 - val_mean_absolute_error: 5.0372

Epoch 845/1000                                                                      
6174/6174 - 1s - loss: 2.8034 - mean_absolute_error: 2.8034 - val_loss: 4.6547 - val_mean_absolute_error: 4.6547

Epoch 846/1000                                                                      
6174/6174 - 1s - loss: 2.8264 - mean_absolute_error: 2.8264 - val_loss: 4.7216 - val_mean_absolute_error: 4.7216

Epoch 847/1000                                                                      
6174/6174 - 1s - loss: 2.8311 - mean_absolute_error: 2.8311 - val_loss: 4.6709 - val_mean_absolute_error: 4.6709

Epoch 848/1000                                                                      
6174/6174 - 1s - loss: 2.8622 - mean_absolute_error: 2.8622 - val_loss: 4.6724 - val_mean_absolute_error: 4.6724

Epoch

Epoch 885/1000                                                                      
6174/6174 - 1s - loss: 2.7728 - mean_absolute_error: 2.7728 - val_loss: 4.7732 - val_mean_absolute_error: 4.7732

Epoch 886/1000                                                                      
6174/6174 - 1s - loss: 2.7722 - mean_absolute_error: 2.7722 - val_loss: 4.8259 - val_mean_absolute_error: 4.8259

Epoch 887/1000                                                                      
6174/6174 - 1s - loss: 2.7834 - mean_absolute_error: 2.7834 - val_loss: 4.6148 - val_mean_absolute_error: 4.6148

Epoch 888/1000                                                                      
6174/6174 - 1s - loss: 2.7535 - mean_absolute_error: 2.7535 - val_loss: 4.6092 - val_mean_absolute_error: 4.6092

Epoch 889/1000                                                                      
6174/6174 - 1s - loss: 2.7932 - mean_absolute_error: 2.7932 - val_loss: 4.6772 - val_mean_absolute_error: 4.6772

Epoch

Epoch 926/1000                                                                      
6174/6174 - 1s - loss: 2.7640 - mean_absolute_error: 2.7640 - val_loss: 4.7304 - val_mean_absolute_error: 4.7304

Epoch 927/1000                                                                      
6174/6174 - 1s - loss: 2.7518 - mean_absolute_error: 2.7518 - val_loss: 4.7274 - val_mean_absolute_error: 4.7274

Epoch 928/1000                                                                      
6174/6174 - 1s - loss: 2.7346 - mean_absolute_error: 2.7346 - val_loss: 4.5762 - val_mean_absolute_error: 4.5762

Epoch 929/1000                                                                      
6174/6174 - 1s - loss: 2.7300 - mean_absolute_error: 2.7300 - val_loss: 4.7329 - val_mean_absolute_error: 4.7329

Epoch 930/1000                                                                      
6174/6174 - 1s - loss: 2.7341 - mean_absolute_error: 2.7341 - val_loss: 4.6711 - val_mean_absolute_error: 4.6711

Epoch

Epoch 967/1000                                                                      
6174/6174 - 1s - loss: 2.7284 - mean_absolute_error: 2.7284 - val_loss: 4.6721 - val_mean_absolute_error: 4.6721

Epoch 968/1000                                                                      
6174/6174 - 1s - loss: 2.7350 - mean_absolute_error: 2.7350 - val_loss: 4.6393 - val_mean_absolute_error: 4.6393

Epoch 969/1000                                                                      
6174/6174 - 1s - loss: 2.7187 - mean_absolute_error: 2.7187 - val_loss: 4.6293 - val_mean_absolute_error: 4.6293

Epoch 970/1000                                                                      
6174/6174 - 1s - loss: 2.7243 - mean_absolute_error: 2.7243 - val_loss: 4.6183 - val_mean_absolute_error: 4.6183

Epoch 971/1000                                                                      
6174/6174 - 1s - loss: 2.7094 - mean_absolute_error: 2.7094 - val_loss: 4.8002 - val_mean_absolute_error: 4.8002

Epoch

In [8]:
print(best_run)

{'Activation': 0, 'Activation_1': 0, 'Activation_2': 0, 'Activation_3': 0, 'Dense': 0, 'Dense_1': 0, 'Dense_2': 1, 'Dense_3': 1, 'Dropout': 0.13767250069394085, 'Dropout_1': 0.5111896818337897, 'Dropout_2': 0.7054140315922363, 'Dropout_3': 1, 'Dropout_4': 0.01305834864014449, 'batch_size': 0, 'choiceval': 2, 'lr': 1, 'lr_1': 0, 'lr_2': 0}


In [9]:
X_train, X_val, X_test, Y_train, Y_val, Y_test = data()

In [32]:
X_val.shape

(686, 20)

In [10]:
best_model.evaluate(X_test, Y_test, verbose=0)

[4.22715711656123, 4.227157]

In [11]:
best_model.summary()

Model: "sequential_24"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_101 (Dense)            (None, 256)               5376      
_________________________________________________________________
activation_101 (Activation)  (None, 256)               0         
_________________________________________________________________
dropout_77 (Dropout)         (None, 256)               0         
_________________________________________________________________
dense_102 (Dense)            (None, 256)               65792     
_________________________________________________________________
activation_102 (Activation)  (None, 256)               0         
_________________________________________________________________
dropout_78 (Dropout)         (None, 256)               0         
_________________________________________________________________
dense_103 (Dense)            (None, 512)             

### Evaluation Metrics

In [12]:
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import r2_score

In [13]:
best_model.predict(X_train)

array([[41.344208],
       [26.009108],
       [25.523378],
       ...,
       [24.894197],
       [14.355597],
       [17.16784 ]], dtype=float32)

In [14]:
Y_train

2917    44.0
845     28.0
6296    25.0
2058    39.0
151     22.0
        ... 
1935    40.0
7335    11.0
5306    25.0
6092    23.0
3468    25.0
Name: tsr, Length: 6174, dtype: float64

In [15]:
Y_train_pred = best_model.predict(X_train).flatten()
print('train MAE', mean_absolute_error(Y_train_pred, Y_train))
print('train r2', r2_score(Y_train, Y_train_pred))

train MAE 3.2882653132278943
train r2 0.8455708951777141


In [16]:
Y_test_pred = best_model.predict(X_test).flatten()
print('test MAE', mean_absolute_error(Y_test_pred, Y_test))
print('test r2', r2_score(Y_test, Y_test_pred))

test MAE 4.227157099062619
test r2 0.7707337754932932


In [19]:
ffnn_y_test_eus = pd.DataFrame(
    {'tsr': Y_test,
     'tsr_predicted': Y_test_pred})
ffnn_y_test_eus.to_sql(name='ffnn_y_test_eus', con=engine, schema='predictor', if_exists='replace', index=False)

### Make TSR predictions using the full dataset

In [18]:
localhost = {'user': 'postgres', 'password': 'postgres', 'host': 'localhost', 'port': 5432, 'db': 'fiadb'}
params = 'postgresql://{0}:{1}@{2}:{3}/{4}'
engine = create_engine(params.format(localhost['user'], localhost['password'], localhost['host'], localhost['port'], localhost['db']))
pergrid_base = """select distinct * from predictor.pergrid_base_eus"""
pergrid_base_df = pd.read_sql(pergrid_base, engine)

# separate predictor variables from outcome varaible
y = pergrid_base_df['tsr']
grid_id = pergrid_base_df['grid_id']
pred_var= ['aet', 'ai', 'art', 'ewd', 'fa', 'map', 'mat', 'mpdq',
       'mtcq', 'pet', 'psn', 'ra', 'rmap', 'rmat', 'tsn', 'mfdf', 'alt','shg','mtwq','wa']
pergrid_base_pred_df = pergrid_base_df[pred_var]

# fill NaN with values from neighbor pixels
imputer = KNNImputer(n_neighbors=5)
pergrid_base_filled = imputer.fit_transform(pergrid_base_pred_df)
pergrid_base_df = pd.DataFrame(pergrid_base_filled)
pergrid_base_df.head()

ss = MinMaxScaler()
X_std = ss.fit_transform(pergrid_base_df)

Xstd=pd.DataFrame(data=X_std[0:,0:],
                index=pergrid_base_pred_df.index,
                columns=pred_var)

In [20]:
# test_predictions = model.predict(normed_test_data).flatten()
y_pred = best_model.predict(Xstd).flatten()

### Ingest TSR predictions to PG

In [21]:
pergrid_all_predicted = pd.DataFrame(
    {'grid_id': grid_id,
     'tsr': y,
     'tsr_predicted': y_pred})

In [22]:
pergrid_all_predicted.head()

grid_id   tsr  tsr_predicted
0      195   5.0       4.012343
1      656   1.0       6.086257
2      657   6.0       5.568583
3      659  10.0       4.100572
4      660   3.0       4.924609

In [29]:
pergrid_base_df.shape

(7623, 20)

In [24]:
pergrid_all_predicted.to_sql(name='ffnn_eus', con=engine, schema='predictor', if_exists='replace', index=False)

In [25]:
update_geom = """
alter table predictor.ffnn_eus add column if not exists wkb_geometry geometry(Polygon,4269);
update predictor.ffnn_eus A SET wkb_geometry = B.wkb_geometry
FROM predictor.pergrid_base B
WHERE A.grid_id = B.grid_id
"""

In [26]:
connection = engine.connect()
connection.execute(update_geom)

In [27]:
update_residual = """
alter table predictor.ffnn_eus add column residual double precision;
update predictor.ffnn_eus set residual = (tsr_predicted-tsr);
"""

In [28]:
connection = engine.connect()
connection.execute(update_residual)